# 1. Dimensionality Reduction

In [1]:
# Import required libraries
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
import umap.umap_ as umap
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis as LDA
from pathlib import Path
import plotly.graph_objects as go
import seaborn as sns

# Set random seeds for reproducibility
np.random.seed(42)

/Users/jen-hung/Desktop/KTH/mnp-liver/.venv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# Preprocessing function
def preprocess_dataframe(df, nan_threshold=0.5):
    feature_columns = [col for col in df.columns if not col.startswith(('Metadata_', 'Image_'))]
    print("Selected feature columns:", feature_columns)
    print("Number of feature columns:", len(feature_columns))
    
    X = df[feature_columns]
    print("Initial number of rows in X:", X.shape[0])
    print("NaN count per column:\n", X.isna().sum())
    print("Inf count per column:\n", np.isinf(X).sum())
    
    threshold = X.shape[0] * nan_threshold
    valid_columns = [col for col in X.columns if X[col].isna().sum() < threshold and np.isinf(X[col]).sum() < threshold]
    print("Valid columns after filtering (>50% valid data):", valid_columns)
    print("Number of valid columns:", len(valid_columns))
    
    if not valid_columns:
        raise ValueError("No valid columns remain after filtering.")
    
    X = X[valid_columns]
    X = X.replace([np.inf, -np.inf], np.nan)
    X = X.fillna(X.median())
    
    nan_count_after_fill = X.isna().sum().sum()
    print("NaN count after filling with median:", nan_count_after_fill)
    if nan_count_after_fill > 0:
        print("Warning: Some NaN values remain. Filling with zero.")
        X = X.fillna(0)
    
    if X.shape[0] == 0 or X.shape[1] == 0:
        raise ValueError("No rows/columns remain after preprocessing.")
    
    scaler = StandardScaler()
    X_scaled = scaler.fit_transform(X)
    return X_scaled, valid_columns

In [3]:
# Function to convert concentration strings to numerical values (grams)
def convert_concentration(value):
    if pd.isna(value) or value == "":
        return 0.0
    try:
        value = str(value).lower().replace(" ", "")  # Normalize input
        if 'g' in value:
            num = float(value.replace('g', ''))
            return num  # Already in grams
        elif 'mg' in value:
            num = float(value.replace('mg', ''))
            return num * 1e-3  # Convert mg to g
        elif 'ug' in value:
            num = float(value.replace('ug', ''))
            return num * 1e-6  # Convert ug to g
        elif 'ng' in value:
            num = float(value.replace('ng', ''))
            return num * 1e-9  # Convert ng to g
        else:
            return float(value)  # Assume it's already a number (e.g., 0)
    except ValueError:
        return 0.0  # Default to 0 for invalid entries

# Plotting function for dimensionality reduction methods (2D and 3D)
def plot_dimensionality_reduction(X_scaled, df, valid_columns, metadata_column, method_name, title, continuous=True, n_components=2):
    if method_name == 'PCA':
        reducer = PCA(n_components=n_components)
        x_label = 'PC1'
        y_label = 'PC2'
        z_label = 'PC3' if n_components == 3 else None
    elif method_name == 't-SNE':
        reducer = TSNE(n_components=n_components, perplexity=30, learning_rate=200, random_state=42)
        x_label = 't-SNE 1'
        y_label = 't-SNE 2'
        z_label = 't-SNE 3' if n_components == 3 else None
    elif method_name == 'UMAP':
        reducer = umap.UMAP(n_components=n_components, n_neighbors=15, min_dist=0.1, random_state=42)
        x_label = 'UMAP 1'
        y_label = 'UMAP 2'
        z_label = 'UMAP 3' if n_components == 3 else None
    elif method_name == 'LDA':
        labels = df[metadata_column].astype(str)
        reducer = LDA(n_components=n_components)
        X_reduced = reducer.fit_transform(X_scaled, labels)
        x_label = 'LD1'
        y_label = 'LD2'
        z_label = 'LD3' if n_components == 3 else None
    else:
        raise ValueError("Unsupported method")
    
    if method_name != 'LDA':
        X_reduced = reducer.fit_transform(X_scaled)
    
    # 2D Plot
    if n_components == 2:
        fig_2d = go.Figure()
        if continuous:
            concentrations = df[metadata_column].apply(convert_concentration)
            fig_2d.add_trace(go.Scatter(x=X_reduced[:, 0], y=X_reduced[:, 1], mode='markers',
                                        marker=dict(color=concentrations, colorscale='Viridis', showscale=True, colorbar=dict(title=f'{metadata_column} (g)'))))
            title += ' (Continuous)'
        else:
            labels = df[metadata_column].astype(str)
            unique_labels = sorted(labels.unique(), key=convert_concentration, reverse=True)
            color_map = {label: f'rgb({r}, {g}, {b})' for label, (r, g, b) in zip(unique_labels, sns.color_palette('tab10', len(unique_labels)))}
            # Remove the initial full trace and rely on individual traces for both points and legend
            for label in unique_labels:
                mask = labels == label
                fig_2d.add_trace(go.Scatter(
                    x=X_reduced[mask, 0], 
                    y=X_reduced[mask, 1], 
                    mode='markers',
                    marker=dict(color=color_map[label]),
                    name=str(label),
                    showlegend=True
                ))
            fig_2d.update_layout(showlegend=True, legend=dict(itemsizing='constant'))
            title += ' (Categorical)'
        fig_2d.update_layout(title=title + f' (2D, {len(valid_columns)} features)', xaxis_title=x_label, yaxis_title=y_label)
        fig_2d.show()
    
    # 3D Plot (if n_components = 3)
    if n_components == 3:
        fig_3d = go.Figure()
        if continuous:
            concentrations = df[metadata_column].apply(convert_concentration)
            fig_3d.add_trace(go.Scatter3d(x=X_reduced[:, 0], y=X_reduced[:, 1], z=X_reduced[:, 2], mode='markers',
                                          marker=dict(color=concentrations, colorscale='Viridis', showscale=True, colorbar=dict(title=f'{metadata_column} (g)'))))
            title += ' (Continuous)'
        else:
            labels = df[metadata_column].astype(str)
            unique_labels = sorted(labels.unique(), key=convert_concentration, reverse=True)
            color_map = {label: f'rgb({r}, {g}, {b})' for label, (r, g, b) in zip(unique_labels, sns.color_palette('tab10', len(unique_labels)))}
            # Remove the initial full trace and rely on individual traces for both points and legend
            for label in unique_labels:
                mask = labels == label
                fig_3d.add_trace(go.Scatter3d(
                    x=X_reduced[mask, 0], 
                    y=X_reduced[mask, 1], 
                    z=X_reduced[mask, 2], 
                    mode='markers',
                    marker=dict(color=color_map[label]),
                    name=str(label),
                    showlegend=True
                ))
            fig_3d.update_layout(showlegend=True, legend=dict(itemsizing='constant'))
            title += ' (Categorical)'
        fig_3d.update_layout(title=title + f' (3D, {len(valid_columns)} features)', 
                             scene=dict(xaxis_title=x_label, yaxis_title=y_label, zaxis_title=z_label))
        fig_3d.show()

## Load Dataset

In [4]:
# Load data
csv_dir = Path("/Users/jen-hung/Desktop/KTH/mnp-liver/csv/")
hep_path = csv_dir / "hep"
f1 = hep_path / "df_SingleCell_AO_HEPG2_102912.csv"
f2 = hep_path / "df_SingleCell_AO_HEPG2_110341.csv"
f3 = hep_path / "df_SingleCell_AO_HEPG2_231222.csv"

df1 = pd.read_csv(f1, sep=",", header=0)
df2 = pd.read_csv(f2, sep=",", header=0)
df3 = pd.read_csv(f3, sep=",", header=0)

# Preprocess each DataFrame
# dataframes = {'df1': df1, 'df2': df2, 'df3': df3}
dataframes = {'df1': df1}
preprocessed_data = {}

for name, df in dataframes.items():
    print(f"\nPreprocessing {name}...")
    X_scaled, valid_columns = preprocess_dataframe(df)
    preprocessed_data[name] = {'X_scaled': X_scaled, 'valid_columns': valid_columns, 'df': df}

/var/folders/kf/6q75_scn7650xfyhtyvv65140000gn/T/ipykernel_23626/4170729835.py:8: DtypeWarning: Columns (1637) have mixed types. Specify dtype option on import or set low_memory=False.
  df1 = pd.read_csv(f1, sep=",", header=0)
/var/folders/kf/6q75_scn7650xfyhtyvv65140000gn/T/ipykernel_23626/4170729835.py:9: DtypeWarning: Columns (1636) have mixed types. Specify dtype option on import or set low_memory=False.
  df2 = pd.read_csv(f2, sep=",", header=0)
/var/folders/kf/6q75_scn7650xfyhtyvv65140000gn/T/ipykernel_23626/4170729835.py:10: DtypeWarning: Columns (1637) have mixed types. Specify dtype option on import or set low_memory=False.
  df3 = pd.read_csv(f3, sep=",", header=0)



Preprocessing df1...
Selected feature columns: ['Cells_ObjectNumber', 'Cells_AreaShape_Area', 'Cells_AreaShape_BoundingBoxArea', 'Cells_AreaShape_BoundingBoxMaximum_X', 'Cells_AreaShape_BoundingBoxMaximum_Y', 'Cells_AreaShape_BoundingBoxMinimum_X', 'Cells_AreaShape_BoundingBoxMinimum_Y', 'Cells_AreaShape_Center_X', 'Cells_AreaShape_Center_Y', 'Cells_AreaShape_CentralMoment_0_0', 'Cells_AreaShape_CentralMoment_0_1', 'Cells_AreaShape_CentralMoment_0_2', 'Cells_AreaShape_CentralMoment_0_3', 'Cells_AreaShape_CentralMoment_1_0', 'Cells_AreaShape_CentralMoment_1_1', 'Cells_AreaShape_CentralMoment_1_2', 'Cells_AreaShape_CentralMoment_1_3', 'Cells_AreaShape_CentralMoment_2_0', 'Cells_AreaShape_CentralMoment_2_1', 'Cells_AreaShape_CentralMoment_2_2', 'Cells_AreaShape_CentralMoment_2_3', 'Cells_AreaShape_Compactness', 'Cells_AreaShape_ConvexArea', 'Cells_AreaShape_Eccentricity', 'Cells_AreaShape_EquivalentDiameter', 'Cells_AreaShape_EulerNumber', 'Cells_AreaShape_Extent', 'Cells_AreaShape_FormF

## PCA

In [5]:
# Apply dimensionality reduction methods to each DataFrame
metadata_column = 'Metadata_concentration_perliter'
method = 'PCA'

for name, data in preprocessed_data.items():
    if metadata_column in data['df'].columns:
        # 2D plots
        # plot_dimensionality_reduction(data['X_scaled'], data['df'], data['valid_columns'], metadata_column,
        #                                 method, f"{method} of {name}", continuous=True, n_components=2)
        plot_dimensionality_reduction(data['X_scaled'], data['df'], data['valid_columns'], metadata_column,
                                        method, f"{method} of {name}", continuous=False, n_components=2)
        
        # 3D plots
        # plot_dimensionality_reduction(data['X_scaled'], data['df'], data['valid_columns'], metadata_column,
        #                                 method, f"{method} of {name}", continuous=True, n_components=3)
        plot_dimensionality_reduction(data['X_scaled'], data['df'], data['valid_columns'], metadata_column,
                                        method, f"{method} of {name}", continuous=False, n_components=3)
    else:
        print(f"Warning: {metadata_column} not found in {name}.")

## t-SNE

In [ ]:
# Apply dimensionality reduction methods to each DataFrame
metadata_column = 'Metadata_concentration_perliter'
method = 't-SNE'

for name, data in preprocessed_data.items():
    if metadata_column in data['df'].columns:
        # 2D plots
        # plot_dimensionality_reduction(data['X_scaled'], data['df'], data['valid_columns'], metadata_column,
        #                                 method, f"{method} of {name}", continuous=True, n_components=2)
        plot_dimensionality_reduction(data['X_scaled'], data['df'], data['valid_columns'], metadata_column,
                                        method, f"{method} of {name}", continuous=False, n_components=2)
        
        # 3D plots
        # plot_dimensionality_reduction(data['X_scaled'], data['df'], data['valid_columns'], metadata_column,
        #                                 method, f"{method} of {name}", continuous=True, n_components=3)
        plot_dimensionality_reduction(data['X_scaled'], data['df'], data['valid_columns'], metadata_column,
                                        method, f"{method} of {name}", continuous=False, n_components=3)
    else:
        print(f"Warning: {metadata_column} not found in {name}.")

## UMAP

In [ ]:
# Apply dimensionality reduction methods to each DataFrame
metadata_column = 'Metadata_concentration_perliter'
method = 'UMAP'

for name, data in preprocessed_data.items():
    if metadata_column in data['df'].columns:
        # 2D plots
        # plot_dimensionality_reduction(data['X_scaled'], data['df'], data['valid_columns'], metadata_column,
        #                                 method, f"{method} of {name}", continuous=True, n_components=2)
        plot_dimensionality_reduction(data['X_scaled'], data['df'], data['valid_columns'], metadata_column,
                                        method, f"{method} of {name}", continuous=False, n_components=2)
        
        # 3D plots
        # plot_dimensionality_reduction(data['X_scaled'], data['df'], data['valid_columns'], metadata_column,
        #                                 method, f"{method} of {name}", continuous=True, n_components=3)
        plot_dimensionality_reduction(data['X_scaled'], data['df'], data['valid_columns'], metadata_column,
                                        method, f"{method} of {name}", continuous=False, n_components=3)
    else:
        print(f"Warning: {metadata_column} not found in {name}.")

## LDA

In [ ]:
# Apply dimensionality reduction methods to each DataFrame
metadata_column = 'Metadata_concentration_perliter'
method = 'LDA'

for name, data in preprocessed_data.items():
    if metadata_column in data['df'].columns:
        # 2D plots
        # plot_dimensionality_reduction(data['X_scaled'], data['df'], data['valid_columns'], metadata_column,
        #                                 method, f"{method} of {name}", continuous=True, n_components=2)
        plot_dimensionality_reduction(data['X_scaled'], data['df'], data['valid_columns'], metadata_column,
                                        method, f"{method} of {name}", continuous=False, n_components=2)
        
        # 3D plots
        # plot_dimensionality_reduction(data['X_scaled'], data['df'], data['valid_columns'], metadata_column,
        #                                 method, f"{method} of {name}", continuous=True, n_components=3)
        plot_dimensionality_reduction(data['X_scaled'], data['df'], data['valid_columns'], metadata_column,
                                        method, f"{method} of {name}", continuous=False, n_components=3)
    else:
        print(f"Warning: {metadata_column} not found in {name}.")

# 2. Clustering

In [15]:
from sklearn.cluster import KMeans, DBSCAN, AgglomerativeClustering

In [16]:
# Clustering function to apply different methods and visualize results
def perform_clustering(X_reduced, df, metadata_column, method_name, reduction_method, n_clusters=3, eps=0.5, min_samples=5):
    if method_name == 'KMeans':
        clusterer = KMeans(n_clusters=n_clusters, random_state=42)
    elif method_name == 'DBSCAN':
        clusterer = DBSCAN(eps=eps, min_samples=min_samples)
    elif method_name == 'Agglomerative':
        clusterer = AgglomerativeClustering(n_clusters=n_clusters)
    else:
        raise ValueError("Unsupported clustering method")
    
    # Fit the clustering model
    labels = clusterer.fit_predict(X_reduced)
    
    # Visualize clustering results (2D)
    fig = go.Figure()
    unique_labels = np.unique(labels)
    color_map = {label: f'rgb({r}, {g}, {b})' for label, (r, g, b) in zip(unique_labels, sns.color_palette('tab10', len(unique_labels)))}
    
    for label in unique_labels:
        mask = labels == label
        fig.add_trace(go.Scatter(
            x=X_reduced[mask, 0], 
            y=X_reduced[mask, 1], 
            mode='markers',
            marker=dict(color=color_map[label]),
            name=f'Cluster {label}' if label != -1 else 'Noise',
            showlegend=True
        ))
    
    # Set axis labels based on reduction method
    if reduction_method == 'PCA':
        x_label, y_label = 'PC1', 'PC2'
    elif reduction_method == 'LDA':
        x_label, y_label = 'LD1', 'LD2'
    elif reduction_method == 't-SNE':
        x_label, y_label = 't-SNE 1', 't-SNE 2'
    elif reduction_method == 'UMAP':
        x_label, y_label = 'UMAP 1', 'UMAP 2'
    
    fig.update_layout(
        title=f'{method_name} Clustering on {reduction_method} (2D, {len(unique_labels)} clusters)',
        xaxis_title=x_label,
        yaxis_title=y_label,
        showlegend=True,
        legend=dict(itemsizing='constant')
    )
    fig.show()
    
    return labels

In [ ]:
# Apply clustering to reduced data from PCA, LDA, t-SNE, and UMAP
metadata_column = 'Metadata_concentration_perliter'
clustering_methods = ['KMeans', 'DBSCAN', 'Agglomerative']
reduction_methods = ['PCA']
# reduction_methods = ['PCA', 'LDA', 't-SNE', 'UMAP']

for name, data in preprocessed_data.items():
    if metadata_column in data['df'].columns:
        X_scaled = data['X_scaled']
        
        for reduction_method in reduction_methods:
            # Compute reduced data based on the method
            if reduction_method == 'PCA':
                reducer = PCA(n_components=2)
                X_reduced = reducer.fit_transform(X_scaled)
            elif reduction_method == 'LDA':
                labels = data['df'][metadata_column].astype(str)
                reducer = LDA(n_components=2)
                X_reduced = reducer.fit_transform(X_scaled, labels)
            elif reduction_method == 't-SNE':
                reducer = TSNE(n_components=2, perplexity=30, learning_rate=200, random_state=42)
                X_reduced = reducer.fit_transform(X_scaled)
            elif reduction_method == 'UMAP':
                reducer = umap.UMAP(n_components=2, n_neighbors=15, min_dist=0.1, random_state=42)
                X_reduced = reducer.fit_transform(X_scaled)
            
            for cluster_method in clustering_methods:
                if cluster_method == 'KMeans' or cluster_method == 'Agglomerative':
                    labels = perform_clustering(X_reduced, data['df'], metadata_column, cluster_method, reduction_method, n_clusters=3)
                elif cluster_method == 'DBSCAN':
                    labels = perform_clustering(X_reduced, data['df'], metadata_column, cluster_method, reduction_method, eps=0.5, min_samples=5)
                print(f"{cluster_method} clustering labels on {reduction_method} for {name}: {np.unique(labels)}")
    else:
        print(f"Warning: {metadata_column} not found in {name}.")

KMeans clustering labels on PCA for df1: [0 1 2]


DBSCAN clustering labels on PCA for df1: [ -1   0   1   2   3   4   5   6   7   8   9  10  11  12  13  14  15  16
  17  18  19  20  21  22  23  24  25  26  27  28  29  30  31  32  33  34
  35  36  37  38  39  40  41  42  43  44  45  46  47  48  49  50  51  52
  53  54  55  56  57  58  59  60  61  62  63  64  65  66  67  68  69  70
  71  72  73  74  75  76  77  78  79  80  81  82  83  84  85  86  87  88
  89  90  91  92  93  94  95  96  97  98  99 100 101 102 103 104 105 106
 107 108 109 110 111 112 113 114 115 116 117 118 119 120 121 122 123 124
 125 126 127 128 129 130 131 132 133 134 135 136 137 138 139 140 141 142
 143 144 145 146 147 148 149 150 151 152 153 154 155 156 157 158 159 160
 161 162 163 164 165 166 167 168 169 170 171 172 173 174 175 176 177 178
 179 180 181 182 183 184 185 186 187 188 189 190 191 192 193 194 195 196
 197 198 199 200 201 202 203 204 205 206 207 208 209 210 211 212 213 214
 215 216 217 218 219 220 221 222 223 224 225 226 227 228 229 230 231 232
 233 234 2

# 3. Evaluation

In [ ]:
from sklearn.metrics import silhouette_score, adjusted_rand_score, calinski_harabasz_score

In [ ]:
# Evaluation function for clustering results
def evaluate_clustering(X_reduced, labels, df, metadata_column):
    # Convert concentration to categorical labels as ground truth
    true_labels = df[metadata_column].astype(str)
    
    # Silhouette Score
    silhouette_avg = silhouette_score(X_reduced, labels) if len(np.unique(labels)) > 1 else None
    
    # Adjusted Rand Score (requires true labels)
    adjusted_rand = adjusted_rand_score(true_labels, labels) if len(np.unique(labels)) > 1 else None
    
    # Calinski-Harabasz Score
    ch_score = calinski_harabasz_score(X_reduced, labels) if len(np.unique(labels)) > 1 else None
    
    print(f"Evaluation Metrics for Clustering:")
    print(f"Silhouette Score: {silhouette_avg:.4f}" if silhouette_avg is not None else "Silhouette Score: N/A (single cluster)")
    print(f"Adjusted Rand Score: {adjusted_rand:.4f}" if adjusted_rand is not None else "Adjusted Rand Score: N/A (single cluster or no true labels)")
    print(f"Calinski-Harabasz Score: {ch_score:.4f}" if ch_score is not None else "Calinski-Harabasz Score: N/A (single cluster)")
    return silhouette_avg, adjusted_rand, ch_score

In [ ]:
# Evaluate clustering results for each reduction method, clustering method, and dataset
metadata_column = 'Metadata_concentration_perliter'
clustering_methods = ['KMeans', 'DBSCAN', 'Agglomerative']
reduction_methods = ['PCA']
# reduction_methods = ['PCA', 'LDA', 't-SNE', 'UMAP']

for name, data in preprocessed_data.items():
    if metadata_column in data['df'].columns:
        X_scaled = data['X_scaled']
        
        for reduction_method in reduction_methods:
            # Compute reduced data based on the method
            if reduction_method == 'PCA':
                reducer = PCA(n_components=2)
                X_reduced = reducer.fit_transform(X_scaled)
            elif reduction_method == 'LDA':
                labels = data['df'][metadata_column].astype(str)
                reducer = LDA(n_components=2)
                X_reduced = reducer.fit_transform(X_scaled, labels)
            elif reduction_method == 't-SNE':
                reducer = TSNE(n_components=2, perplexity=30, learning_rate=200, random_state=42)
                X_reduced = reducer.fit_transform(X_scaled)
            elif reduction_method == 'UMAP':
                reducer = umap.UMAP(n_components=2, n_neighbors=15, min_dist=0.1, random_state=42)
                X_reduced = reducer.fit_transform(X_scaled)
            
            for cluster_method in clustering_methods:
                if cluster_method == 'KMeans' or cluster_method == 'Agglomerative':
                    labels = perform_clustering(X_reduced, data['df'], metadata_column, cluster_method, reduction_method, n_clusters=3)
                elif cluster_method == 'DBSCAN':
                    labels = perform_clustering(X_reduced, data['df'], metadata_column, cluster_method, reduction_method, eps=0.5, min_samples=5)
                print(f"\nEvaluating {cluster_method} clustering on {reduction_method} for {name}:")
                evaluate_clustering(X_reduced, labels, data['df'], metadata_column)
    else:
        print(f"Warning: {metadata_column} not found in {name}.")